In [178]:
import numpy as np  
import pandas as pd  
from pandas_datareader import data as wb  
import matplotlib.pyplot as plt  
from scipy.stats import norm
%matplotlib inline
pd.options.plotting.backend = "plotly"


In [179]:
high_yield = pd.read_csv('high_yield.txt')
hy_tickers = high_yield['TICKER'].tolist()

stuff_to_remove = ['SHYD','SJB','HYD','KCCB', 'SOVB']
hy_tickers = [x for x in hy_tickers if x not in stuff_to_remove]

hy_tickers.append('SPY')

In [40]:
# data = wb.DataReader(hy_tickers, data_source='yahoo', start='2019-11-01')['Adj Close']
# data.to_pickle('data/hy_etf_ticker_data.pkl')

In [180]:
data = pd.read_pickle('data/hy_etf_ticker_data.pkl')

In [181]:
hyg = data['HYG'].pct_change()[1:]
spy = data['SPY'].pct_change()[1:]

pct_chg = data.pct_change()
pct_chg = pct_chg.iloc[1:]

In [209]:
pct_chg

Symbols          HYG       JNK      HYLB      USHY      SHYG      BKLN  \
Date                                                                     
2019-11-04  0.002073  0.001571  0.002207  0.000492  0.001083  0.001781   
2019-11-05 -0.001035 -0.000830 -0.001201 -0.000737 -0.000433  0.000889   
2019-11-06 -0.001151 -0.001569 -0.001804 -0.000739 -0.000649 -0.001332   
2019-11-07 -0.000461 -0.000185  0.000201 -0.000247 -0.000650  0.001778   
2019-11-08  0.000922  0.000648  0.000402  0.000247  0.000650  0.001332   
...              ...       ...       ...       ...       ...       ...   
2021-01-29 -0.002638 -0.003951 -0.002997 -0.002181 -0.002419 -0.002693   
2021-02-01  0.003208  0.004204 -0.000601  0.002196  0.003807  0.002700   
2021-02-02  0.002416  0.003227  0.003409  0.002921  0.002646  0.000898   
2021-02-03  0.000803  0.000735  0.000200  0.000971  0.000000  0.000000   
2021-02-04  0.002064  0.001561  0.001998  0.001940  0.001759  0.003587   

Symbols         ANGL      SJNK      HYLS      SRLN  ...      HYTR      HYUP  \
Date                                                ...                       
2019-11-04  0.005834  0.002241  0.000830  0.000000  ...       NaN  0.003612   
2019-11-05 -0.001706 -0.001864 -0.001244  0.000437  ...       NaN -0.002275   
2019-11-06 -0.000684 -0.001120 -0.000208 -0.001091  ...       NaN -0.001037   
2019-11-07 -0.001026 -0.000374 -0.000415  0.001092  ...       NaN -0.000166   
2019-11-08  0.000000  0.001122  0.000208  0.001309  ...       NaN  0.000332   
...              ...       ...       ...       ...  ...       ...       ...   
2021-01-29 -0.001867 -0.002956 -0.001639 -0.001740  ... -0.003120 -0.003505   
2021-02-01  0.001189  0.003571  0.000821  0.001968  ...  0.003088 -0.002248   
2021-02-02  0.006252  0.002965  0.001641 -0.000218  ...  0.003661  0.003922   
2021-02-03  0.001243 -0.000370  0.001433 -0.000218  ...  0.000415 -0.000062   
2021-02-04  0.001241  0.001479  0.001636  0.003057  ... -0.000580 -0.000520   

Symbols         BSJS      SEIX      IBHF      FLBL      FLHY      HYHG  \
Date                                                                     
2019-11-04       NaN  0.000404       NaN -0.000604  0.000770  0.002485   
2019-11-05       NaN  0.000607       NaN -0.000604 -0.000500  0.002014   
2019-11-06       NaN  0.000202       NaN  0.000806  0.000500 -0.003092   
2019-11-07       NaN  0.000606       NaN  0.000201 -0.001461  0.003567   
2019-11-08       NaN  0.000202       NaN  0.000604 -0.001425 -0.001082   
...              ...       ...       ...       ...       ...       ...   
2021-01-29 -0.001369 -0.000846 -0.002006 -0.002528 -0.001481 -0.002084   
2021-02-01  0.002350 -0.000766  0.002215  0.003218  0.002853  0.001285   
2021-02-02  0.002032 -0.000403  0.003394 -0.001604  0.004362 -0.003530   
2021-02-03  0.001287  0.001211 -0.000669 -0.001406  0.000567  0.002093   
2021-02-04  0.001644  0.000000 -0.000590  0.001573  0.000189 -0.000612   

Symbols          UJB       SPY  
Date                            
2019-11-04  0.014047  0.004018  
2019-11-05 -0.006926 -0.001106  
2019-11-06 -0.001813  0.000228  
2019-11-07  0.002236  0.003517  
2019-11-08 -0.003904  0.002466  
...              ...       ...  
2021-01-29 -0.002971 -0.020020  
2021-02-01  0.005960  0.016646  
2021-02-02  0.006732  0.014140  
2021-02-03 -0.002006  0.000786  
2021-02-04  0.004355  0.011156  

[316 rows x 64 columns]

In [182]:
import plotly.express as px

fig = px.line(pct_chg)
fig.show()

In [183]:
import statsmodels.api as sm
from statsmodels import regression

beta_frame = []

for ticker in hy_tickers:
    print(ticker)
    x = pct_chg['SPY'].values
    y = pct_chg[ticker].values
    
    x = sm.add_constant(x)
    model = regression.linear_model.OLS(y,x).fit()
    
    x = x[:, 1]
    
    alpha = model.params[0]
    beta = model.params[1]
    
    temp_dict = {
        'alpha' : alpha,
        'beta' : beta,
        'ticker' : ticker
    }
    beta_frame.append(temp_dict)
    
beta_frame = pd.DataFrame(beta_frame)

HYG
JNK
HYLB
USHY
SHYG
BKLN
ANGL
SJNK
HYLS
SRLN
HYS
FTSL
HYMB
BSJL
PHB
BSJM
BSJK
HYEM
BSJN
FALN
PTBD
EMHY
JPHY
PGHY
HYGV
BSJO
GHYG
SPHY
GHYB
FDHY
BSJP
HYZD
HYLV
HYLD
WFHY
IHY
HYBB
HYXF
NUHY
HYGH
BKHY
BSJQ
PHYL
SNLN
KDFI
HYXU
HYDW
HYDB
SHYL
FLRT
FJNK
SFHY
BSJR
ESHY
HYTR
HYUP
BSJS
SEIX
IBHF
FLBL
FLHY
HYHG
UJB
SPY


In [184]:
import plotly.express as px
fig = px.histogram(beta_frame, x="beta")
fig.show()

In [185]:
def calc_beta(pct_chg, ticker):
    x = pct_chg['SPY'].values
    y = pct_chg[ticker].values
    
    x = sm.add_constant(x)
    model = regression.linear_model.OLS(y,x).fit()
    
    x = x[:, 1]
    
    alpha = model.params[0]
    beta = model.params[1]
    
    temp_dict = {
        'alpha' : alpha,
        'beta' : beta,
        'ticker' : ticker
    }
    
    return temp_dict

In [186]:
# data = wb.DataReader(hy_tickers, data_source='yahoo', start='2019-7-1')['Adj Close']


In [187]:
pct_chg = data.pct_change()
pct_chg = pct_chg.iloc[1:]

In [188]:
min_date = data.index.min() + pd.DateOffset(1)

In [189]:
window_start = data.index.min()

window_stop = data.index.max() - pd.DateOffset(60)

window_total = window_stop - window_start
window_total = window_total.days

In [190]:
i = 0
start_date = window_start

rolling_beta_frame = []
while(i <= window_total):
    print(i)
    window_end = start_date + pd.DateOffset(60)
    filtered_pct_chg = pct_chg[(pct_chg.index >= start_date) & 
                        (pct_chg.index < window_end)]
    
    for ticker in hy_tickers:
        temp_dict = calc_beta(filtered_pct_chg, ticker)
        temp_dict['date'] = window_end
        rolling_beta_frame.append(temp_dict)
        
    print(start_date)
    
    i+=1
    start_date = start_date + pd.DateOffset(1)

0
2019-11-01 00:00:00
1
2019-11-02 00:00:00
2
2019-11-03 00:00:00
3
2019-11-04 00:00:00
4
2019-11-05 00:00:00
5
2019-11-06 00:00:00
6
2019-11-07 00:00:00
7
2019-11-08 00:00:00
8
2019-11-09 00:00:00
9
2019-11-10 00:00:00
10
2019-11-11 00:00:00
11
2019-11-12 00:00:00
12
2019-11-13 00:00:00
13
2019-11-14 00:00:00
14
2019-11-15 00:00:00
15
2019-11-16 00:00:00
16
2019-11-17 00:00:00
17
2019-11-18 00:00:00
18
2019-11-19 00:00:00
19
2019-11-20 00:00:00
20
2019-11-21 00:00:00
21
2019-11-22 00:00:00
22
2019-11-23 00:00:00
23
2019-11-24 00:00:00
24
2019-11-25 00:00:00
25
2019-11-26 00:00:00
26
2019-11-27 00:00:00
27
2019-11-28 00:00:00
28
2019-11-29 00:00:00
29
2019-11-30 00:00:00
30
2019-12-01 00:00:00
31
2019-12-02 00:00:00
32
2019-12-03 00:00:00
33
2019-12-04 00:00:00
34
2019-12-05 00:00:00
35
2019-12-06 00:00:00
36
2019-12-07 00:00:00
37
2019-12-08 00:00:00
38
2019-12-09 00:00:00
39
2019-12-10 00:00:00
40
2019-12-11 00:00:00
41
2019-12-12 00:00:00
42
2019-12-13 00:00:00
43
2019-12-14 00:00:0

2020-10-22 00:00:00
357
2020-10-23 00:00:00
358
2020-10-24 00:00:00
359
2020-10-25 00:00:00
360
2020-10-26 00:00:00
361
2020-10-27 00:00:00
362
2020-10-28 00:00:00
363
2020-10-29 00:00:00
364
2020-10-30 00:00:00
365
2020-10-31 00:00:00
366
2020-11-01 00:00:00
367
2020-11-02 00:00:00
368
2020-11-03 00:00:00
369
2020-11-04 00:00:00
370
2020-11-05 00:00:00
371
2020-11-06 00:00:00
372
2020-11-07 00:00:00
373
2020-11-08 00:00:00
374
2020-11-09 00:00:00
375
2020-11-10 00:00:00
376
2020-11-11 00:00:00
377
2020-11-12 00:00:00
378
2020-11-13 00:00:00
379
2020-11-14 00:00:00
380
2020-11-15 00:00:00
381
2020-11-16 00:00:00
382
2020-11-17 00:00:00
383
2020-11-18 00:00:00
384
2020-11-19 00:00:00
385
2020-11-20 00:00:00
386
2020-11-21 00:00:00
387
2020-11-22 00:00:00
388
2020-11-23 00:00:00
389
2020-11-24 00:00:00
390
2020-11-25 00:00:00
391
2020-11-26 00:00:00
392
2020-11-27 00:00:00
393
2020-11-28 00:00:00
394
2020-11-29 00:00:00
395
2020-11-30 00:00:00
396
2020-12-01 00:00:00
397
2020-12-02 00:00

In [191]:
rolling_beta = pd.DataFrame(rolling_beta_frame)

In [192]:
rolling_beta.index = rolling_beta['date']

In [193]:
rolling_beta = rolling_beta[['alpha','beta','ticker']]

In [194]:
rolling_beta = rolling_beta.reset_index()

rolling_beta

date         alpha      beta ticker
0     2019-12-31  1.773398e-04  0.237195    HYG
1     2019-12-31  2.069934e-04  0.227684    JNK
2     2019-12-31  1.726552e-04  0.236544   HYLB
3     2019-12-31  2.609138e-04  0.192474   USHY
4     2019-12-31  1.142766e-04  0.166085   SHYG
...          ...           ...       ...    ...
25723 2021-02-04  3.129296e-04  0.116153   FLBL
25724 2021-02-04  2.139628e-04  0.138485   FLHY
25725 2021-02-04 -2.294909e-05  0.131576   HYHG
25726 2021-02-04  2.960707e-04  0.274733    UJB
25727 2021-02-04  2.168404e-19  1.000000    SPY

[25728 rows x 4 columns]

In [195]:
rolling_b = rolling_beta.pivot(index='date', columns='ticker', values='beta')

In [196]:
import plotly.express as px

fig = px.line(rolling_b)
fig.show()

# AVERAGE BETA FOR CORPORATE BOND ETFS OVER TIME

In [198]:
rolling_b.mean(axis=1).reset_index().plot.line('date',0)

In [61]:
gme_data = wb.DataReader(['GME'], data_source='yahoo', start='2020-1-1')['Volume']

In [62]:
gme_data[gme_data.index >= '03/02/2020'].plot.line()

In [199]:
import os
files = os.listdir('corporate_bond_data/')
files = ['corporate_bond_data/' + x for x in files]

frame_list = []

for file in files:
    fname = file.split('/')[1]
    finfo = fname.split('.')[0]
    
    firm_name = finfo.split('_')[0]
    rating = finfo.split('_')[1]
    industry = finfo.split('_')[2]
    
    temp_data = pd.read_excel(file)
    temp_data['company_name'] = firm_name
    temp_data['rating'] = rating
    temp_data['industry'] = industry
    frame_list.append(temp_data)
    
bond_data = pd.concat(frame_list)

In [200]:
bond_data['company_name'].value_counts()

bedbathbeyond       726
macys               724
royalcarribean      631
goldennugget        613
boeing              450
lionsgate           411
americanairlines    385
cinemark            235
hertz               216
Name: company_name, dtype: int64

In [201]:
bond_mapping = {
    'bedbathbeyond':'BBBY',
    'macys' : 'M',
    'royalcarribean' : 'RCL',
    'goldennugget' : 'GNOG',
    'boeing' : 'BA',
    'lionsgate' : 'LGF.A',
    'americanairlines' : 'AAL',
    'cinemark': 'CNK',
    'hertz' : 'HTZGQ'
}

bond_data['ticker'] = bond_data['company_name'].map(bond_mapping)

bond_ticker_list = list(bond_mapping.values())

In [202]:
bond_ticker_data = wb.DataReader(bond_ticker_list, data_source='yahoo', start='2019-11-01')['Adj Close']
bond_ticker_data.to_pickle('data/bond_ticker_data.pkl')

/Users/paulrice/opt/anaconda3/lib/python3.8/site-packages/pandas_datareader/base.py:272: SymbolWarning:

Failed to read symbol: 'LGF.A', replacing with NaN.



In [203]:
bond_ticker_data = pd.read_pickle('data/bond_ticker_data.pkl')

# Here we visualize our bond prices over time. My favorite one is hertz.

In [204]:
bond_data.plot.line('Date','Indicative',color='company_name')

In [205]:
pivot_bond_data = bond_data.pivot_table(index='Date', columns='ticker', values='Indicative')


In [206]:
corr_frame = []

for ticker in bond_ticker_list:
    temp_bonds = pivot_bond_data[[ticker]].pct_change()
    temp_bonds = temp_bonds[temp_bonds[ticker].notnull()].reset_index()
    temp_stocks = bond_ticker_data[[ticker]].pct_change()
    temp_stocks = temp_stocks[temp_stocks[ticker].notnull()].reset_index()
    
    
    stock_bond = pd.merge(temp_stocks, temp_bonds, how='left', on='Date')
    stock_bond = stock_bond[(stock_bond[ticker+'_x'].notnull()) & 
                            (stock_bond[ticker+'_y'].notnull())]
    
#     stock_bond['rolling_corr'] = stock_bond[ticker+'_x'].rolling(30).corr(stock_bond[ticker+'_y'])    
    stock_bond['rolling_corr'] = stock_bond[ticker+'_y'].rolling(40).corr(stock_bond[ticker+'_x'])    
    stock_bond['ticker'] = ticker
    
    corr_frame.append(stock_bond)

In [207]:
corr_frame = pd.concat(corr_frame)

corr_frame.plot.line('Date','rolling_corr', color='ticker')

In [170]:
bond_ticker_data.reset_index().plot.line('Date','BA')